Finding hash values of frames with time stamp and ssim between frames
MEan of time stamp is found out and hash values are calculated

In [ ]:
!ffmpeg -debug mb_type -i '/content/01_original.mp4' '/content/output.mp4'

ffmpeg version 4.2.7-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 9 (Ubuntu 9.4.0-1ubuntu1~20.04.1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-avresample --disable-filter=resample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librsvg --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --e

In [ ]:
import cv2
import os
out_dir_path='/content/frames'
if not os.path.exists(out_dir_path):
 os.mkdir('/content/frames')
vidcap = cv2.VideoCapture('/content/01_original.mp4')
def getFrame(sec):
    vidcap.set(cv2.CAP_PROP_POS_MSEC,sec*1000)
    hasFrames,image = vidcap.read()
    video_length = round(vidcap.get(cv2.CAP_PROP_FRAME_COUNT)) - 1
    video_fps = round(vidcap.get(cv2.CAP_PROP_FPS),2)
    video_time = round((video_length /video_fps),2)
    video_resolution = str(vidcap.get(cv2.CAP_PROP_FRAME_WIDTH)) + "/" + str(vidcap.get(cv2.CAP_PROP_FRAME_HEIGHT ))
    if hasFrames:
        cv2.imwrite("/content/frames/image"+str(count)+".jpg", image)     # save frame as JPG file
    return hasFrames
sec = 0
frameRate = 0.5 #//it will capture image in each 0.5 second
count=1
success = getFrame(sec)
while success:
    count = count + 1
    sec = sec + frameRate
    sec = round(sec, 2)
    success = getFrame(sec)

In [ ]:
from os import listdir
from os.path import isfile, join
import numpy
import cv2
import natsort
from skimage.metrics import structural_similarity as ssim
mypath='/content/frames'
onlyfiles = [ f for f in listdir(mypath) if isfile(join(mypath,f)) ]
onlyfiles=natsort.natsorted(onlyfiles)
images = numpy.empty(len(onlyfiles), dtype=object)
ssim_list=[]
for n in range(0, len(onlyfiles)):
  images[n] = cv2.imread( join(mypath,onlyfiles[n]) )
for n in range(0,len(images)-1):
  img1=images[n]
  img2=images[n+1]
  image1 = cv2.cvtColor(img1, cv2.COLOR_BGR2GRAY)
  image2 = cv2.cvtColor(img2, cv2.COLOR_BGR2GRAY)          # trainImage
  score, diff = ssim(image1, image2, full=True)
  print("SSIM between frames: {} "+ str(n) + " and " + str(n+1)+" is "+ format(score))
  print(type(score))
  ssim_list.append(score)
  ssim_array=numpy.array(ssim_list)
 # ssim_tuple=tuple(ssim_list)
print(type(ssim_array))

SSIM between frames: {} 0 and 1 is 0.4594462286486888
<class 'numpy.float64'>
SSIM between frames: {} 1 and 2 is 0.5226482775250323
<class 'numpy.float64'>
SSIM between frames: {} 2 and 3 is 0.47657965379283473
<class 'numpy.float64'>
SSIM between frames: {} 3 and 4 is 0.5359406774843043
<class 'numpy.float64'>
SSIM between frames: {} 4 and 5 is 0.5601857898346957
<class 'numpy.float64'>
SSIM between frames: {} 5 and 6 is 0.6043646384752362
<class 'numpy.float64'>
SSIM between frames: {} 6 and 7 is 0.6082616974468726
<class 'numpy.float64'>
SSIM between frames: {} 7 and 8 is 0.5559660128086505
<class 'numpy.float64'>
SSIM between frames: {} 8 and 9 is 0.6410908906239154
<class 'numpy.float64'>
SSIM between frames: {} 9 and 10 is 0.6765190748395087
<class 'numpy.float64'>
SSIM between frames: {} 10 and 11 is 0.631700232027822
<class 'numpy.float64'>
SSIM between frames: {} 11 and 12 is 0.6627062109161389
<class 'numpy.float64'>
SSIM between frames: {} 12 and 13 is 0.522329941592637
<cla

In [ ]:
!pip install moviepy

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install imageio==2.4.1

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 48.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for imageio: filename=imageio-2.4.1-py3-none-any.whl size=3303886 sha256=677d546a30344f8614b449904241f69b68faaf2280cf4fe12f9b08180465f676
  Stored in directory: /root/.cache/pip/wheels/b7/44/b7/2e7cc9c5fe4a893b9cc83a010d4410557bedf6cf3b5829f497
Successfully built imageio
  Attempting uninstall: imageio
    Found existing installation: imageio 2.9.0
    Uninstalling imageio-2.9.0:
      Successfully uninstalled imageio-2.9.0


In [ ]:
import sys
import numpy as np
import cv2
import moviepy.editor as mpy
from matplotlib import pyplot as plt

vid = mpy.VideoFileClip('/content/01_original.mp4')
time_stamp=[]
average=[]
for i, (tstamp, frame) in enumerate(vid.iter_frames(with_times=True)):
  #print("Frame no: "+str(i)+" with time stamp "+str(round(tstamp%60,2)))
  time_stamp.insert(i,round(tstamp%60,2))
  #avg=sum(i,i+1)/2
for x in time_stamp:
  for y in time_stamp:
    sum=x+y
    avg=sum/2
    average.append(avg)
print(time_stamp)
#average_tuple=tuple(average)#converting list to tuple
avg_array=numpy.array(average)
print(type(avg_array))
#print(type(average_tuple))
  #print(i)
   
    #plt.imshow(frame)
   # plt.show()

[0.0, 0.04, 0.08, 0.12, 0.16, 0.2, 0.24, 0.28, 0.32, 0.36, 0.4, 0.44, 0.48, 0.52, 0.56, 0.6, 0.64, 0.68, 0.72, 0.76, 0.8, 0.84, 0.88, 0.92, 0.96, 1.0, 1.04, 1.08, 1.12, 1.16, 1.2, 1.24, 1.28, 1.32, 1.36, 1.4, 1.44, 1.48, 1.52, 1.56, 1.6, 1.64, 1.68, 1.72, 1.76, 1.8, 1.84, 1.88, 1.92, 1.96, 2.0, 2.04, 2.08, 2.12, 2.16, 2.2, 2.24, 2.28, 2.32, 2.36, 2.4, 2.44, 2.48, 2.52, 2.56, 2.6, 2.64, 2.68, 2.72, 2.76, 2.8, 2.84, 2.88, 2.92, 2.96, 3.0, 3.04, 3.08, 3.12, 3.16, 3.2, 3.24, 3.28, 3.32, 3.36, 3.4, 3.44, 3.48, 3.52, 3.56, 3.6, 3.64, 3.68, 3.72, 3.76, 3.8, 3.84, 3.88, 3.92, 3.96, 4.0, 4.04, 4.08, 4.12, 4.16, 4.2, 4.24, 4.28, 4.32, 4.36, 4.4, 4.44, 4.48, 4.52, 4.56, 4.6, 4.64, 4.68, 4.72, 4.76, 4.8, 4.84, 4.88, 4.92, 4.96, 5.0, 5.04, 5.08, 5.12, 5.16, 5.2, 5.24, 5.28, 5.32, 5.36, 5.4, 5.44, 5.48, 5.52, 5.56, 5.6, 5.64, 5.68, 5.72, 5.76, 5.8, 5.84, 5.88, 5.92, 5.96, 6.0, 6.04, 6.08, 6.12, 6.16, 6.2, 6.24, 6.28, 6.32, 6.36, 6.4, 6.44, 6.48, 6.52, 6.56, 6.6, 6.64, 6.68, 6.72, 6.76, 6.8, 6.84, 6.

In [ ]:
!ffmpeg -i '/content/alas walk1.AVI' -vf "shuffleframes=0 1 1 1 1 1" '/content/forged_1.avi'

ffmpeg version 4.2.7-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 9 (Ubuntu 9.4.0-1ubuntu1~20.04.1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-avresample --disable-filter=resample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librsvg --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --e

In [ ]:
#taking first 15 frames in tuple
avg_tuple=average_tuple[0:len(ssim_tuple)]
covariance=[]
print(type(ssim_tuple))
print(avg_tuple)
#hash(avg_tuple)
for i in range(0,len(ssim_tuple)):
  for j in range(0,len(avg_tuple)):
    #cov_mat = np.stack((x, y), axis = 0)
     covariance=numpy.cov(ssim_tuple[i],avg_tuple[j])
print(covariance)
    

  covariance=numpy.cov(ssim_tuple[i],avg_tuple[j])

  c *= np.true_divide(1, fact)

  c *= np.true_divide(1, fact)



<class 'tuple'>
(0.0, 0.02, 0.04, 0.06, 0.08, 0.1, 0.12, 0.14, 0.16, 0.18, 0.2, 0.22, 0.24, 0.26, 0.28, 0.3)
[[nan nan]
 [nan nan]]


Finding co variance between two different arrays 
REference https://www.geeksforgeeks.org/python-numpy-cov-function/

In [ ]:
avg_array=avg_array[0:len(ssim_array)]
cov_mat = numpy.stack((ssim_array,avg_array), axis = 0)
 
print(numpy.cov(cov_mat))

[[0.00446079 0.00445381]
 [0.00445381 0.00906667]]


Finding corelation between two variables 
Reference https://www.statology.org/correlation-in-python/ and
https://numpy.org/doc/stable/reference/routines.statistics.html

In [ ]:
np.corrcoef(avg_array, ssim_array)
np.corrcoef(avg_array, ssim_array)[0,1]

0.70032866364079

Reference https://numpy.org/doc/stable/reference/generated/numpy.convolve.html
Working of numpy.convolve reference
https://stackoverflow.com/questions/20036663/understanding-numpys-convolve

In [ ]:
avrg_array=avg_array[0:len(ssim_array)]
conv_array=np.convolve(avrg_array,ssim_array,'same')
print(conv_array)
print(len(conv_array))

[0.28752445 0.37399231 0.47328199 0.58610205 0.71155611 0.8502643
 0.99941909 1.16048421 1.33434561 1.37414319 1.38452718 1.39920017
 1.38534604 1.35301466 1.29534233 1.22433565]
16


Reference https://numpy.org/doc/stable/reference/generated/numpy.correlate.html#numpy.correlate

In [ ]:
cor_array=np.correlate(conv_array,conv_array,"same")
len(cor_array)

16

In [ ]:
os.mkdir('/content/conv_frames')
from PIL import Image
conv_array = conv_array.astype(np.uint8)
for i in range(len(conv_array)):
  image=Image.fromarray(conv_array)
  image.save("/content/conv_frames/conv_Image"+str(i)+".jpg")

In [ ]:
np.convolve([1,2,3],[1,2,3],'same')

array([ 4, 10, 12])

Custom hash value in Python Reference https://www.geeksforgeeks.org/python-hash-method/

In [ ]:
class Emp:
    def __init__(self, emp_name, id):
        self.emp_name = emp_name
        self.id = id
 
    def __eq__(self, other):
       
        # Equality Comparison between two objects
        return self.emp_name == other.emp_name and self.id == other.id
 
    def __hash__(self):
       
        # hash(custom_object)
        return hash((self.emp_name, self.id))
for i in range(0,len(ssim_tuple)):
  emp = Emp(ssim_tuple[i], avg_tuple[i])
  print("The hash is: %s" % hash(emp))
 
# We'll check if two objects with the same
# attribute values have the same hash
#emp_copy = Emp('Ragav', 12)
#print("The hash is: %d" % hash(emp_copy))

The hash is: -1940880510470153369
The hash is: -2782829697880447710
The hash is: -8215297085580803056
The hash is: -737501966513205322
The hash is: 5707072888978533568
The hash is: -2864106650792462787
The hash is: 1233885389219509938
The hash is: 183027146659205637
The hash is: 2601812569226692780
The hash is: 1877569780287744078
The hash is: -5823591950989639284
The hash is: 2931505212490732719
The hash is: 401587173520574850
The hash is: 8164257707046587456
The hash is: -6415669066761246535


In [ ]:
!pip install distance

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 180.3/180.3 KB 4.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for distance: filename=Distance-0.1.3-py3-none-any.whl size=16275 sha256=0dd50e9f85bc89e3b5d05b2a311765c42a158811fd043196f4078537c0b165d7
  Stored in directory: /root/.cache/pip/wheels/fb/b3/aa/04241cced6d1722b132273b1d6aafba317887ec004f48b853a
Successfully built distance


In [ ]:
import difflib
difflib.SequenceMatcher('-1940880510470153369','-1940880510470153369').ratio()

0.0

In [ ]:
import distance
distance.hamming(8164257707046587456,-6415669066761246535)

TypeError: ignored

In [ ]:
!pip install hexhamming

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.8/42.8 KB 2.2 MB/s eta 0:00:00


In [ ]:
print(len( 2931505212490732719))

TypeError: ignored

In [ ]:
from hexhamming import hamming_distance_string
#hamming_distance_string("-1940880510470153369", "-2782829697880447710")
hamming_distance_string("1877569780287744078", "-5823591950989639284")

ValueError: ignored

In [ ]:
class Emp:
    def __init__(self, avg, ssim):
        self.avg = avg
        self.ssim = ssim
 
    def __eq__(self, other):
       
        # Equality Comparison between two objects
        return self.avg == other.avg and self.ssim == other.ssim
 
    def __hash__(self):
       
        # hash(custom_object)
        return hash((self.avg, self.ssim))
 
emp = Emp('Ragav', 12)
print("The hash is: %d" % hash(emp))
 
# We'll check if two objects with the same
# attribute values have the same hash
emp_copy = Emp('Ragav', 12)
print("The hash is: %d" % hash(emp_copy))

The hash is: -5025028378723065384
The hash is: -5025028378723065384
